# Enfermedades mentales en tecnología
## Facultad TIC Universidad Pontificia Bolivariana <a class="tocSkip">

**Estudiante:** Nathalia Andrea Ortega Gómez

**ID:** 000200550

**Email:** nathalia.ortega@upb.edu.co

**Fecha de Entrega: 22 de Octubre de 2020**

## Introducción

Cada año, [OSMI](https://osmihelp.org/) (open sourcing mental illness) realiza una encuesta a gran escala sobre la prevalencia y las actitudes hacia la salud mentall de las personas que trabajan en la industria tecnológica.

Las posibles salidas para la predicción son:
- Yes (tiene actualmente una enfermedad mental)
- No (No tiene una enfermedad mental)

## Objetivo principal
** Predecir qué empleados tienen más probabilidad de padecer una enfermedad mental. **

## Información de los datos
El dataset original contiene muchos datos faltantes, redundantes y ruidosos como es de esperarse en los datos del mundo real.

El dataset original, contenía como encabezados las preguntas de la encuesta, las cuales fueron transformadas a nombres más pequeños y discientes. A pesar de que, existen columnas con su mayoría de registros vacíos.

## dataset
Se unieron dos datsets de la misma encuesta ([las respuestas para el 2017](https://www.kaggle.com/osmihelp/osmi-mental-health-in-tech-survey-2017) y las [respuestas para el 2018](https://www.kaggle.com/osmihelp/osmi-mental-health-in-tech-survey-2018)) teniendo en cuenta que ambas contienen las mismas preguntas y que cada una cuenta con más de 500 registros.

# Importar librerías

In [1]:
pip install pandas


You should consider upgrading via the 'C:\Users\natya\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.



In [2]:
pip install numpy


You should consider upgrading via the 'C:\Users\natya\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.


In [3]:
pip install matplotlib


You should consider upgrading via the 'C:\Users\natya\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.


In [4]:
pip install seaborn

Note: you may need to restart the kernel to use updated packages.Requirement already satisfied: numpy>=1.15 in c:\users\natya\appdata\local\programs\python\python38\lib\site-packages (from seaborn) (1.19.2)

You should consider upgrading via the 'C:\Users\natya\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.


In [5]:
pip install sklearn


You should consider upgrading via the 'C:\Users\natya\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.


In [6]:
pip install pandas_profiling


You should consider upgrading via the 'C:\Users\natya\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.


In [7]:
pip install scipy

You should consider upgrading via the 'C:\Users\natya\AppData\Local\Programs\Python\Python38\python.exe -m pip install --upgrade pip' command.



In [22]:
import pandas as pd
import numpy as np
import seaborn as sns
import csv
from googletrans import Translator
%matplotlib inline
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
import scipy.stats as stats
from scipy.stats import chi2_contingency
from sklearn.model_selection import train_test_split
from sklearn import model_selection
import plotly.express as px

# Cargar los datos

In [9]:
mentalHealth_data = pd.read_csv("../data/processed/data_imbalanced.csv")

In [10]:
mentalHealth_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 663 entries, 0 to 662
Data columns (total 34 columns):
 #   Column                                      Non-Null Count  Dtype  
---  ------                                      --------------  -----  
 0   No_empleados                                663 non-null    object 
 1   cubrimiento_EM                              663 non-null    object 
 2   concimiento_cubrimiento_EM                  663 non-null    int64  
 3   recursos_EM                                 663 non-null    object 
 4   dejar_trabajo_EM                            663 non-null    object 
 5   habla_jefe_EM_flag                          663 non-null    float64
 6   hablar_companeros_EM_flag                   663 non-null    float64
 7   hablar_companeros_EM_conmigo                663 non-null    float64
 8   importacia_salud_fisica                     663 non-null    float64
 9   importancia_salud_mental                    663 non-null    float64
 10  trabajado_otra

## Conversión de variables

In [11]:
cat_cols = list(mentalHealth_data.select_dtypes('object').columns)
class_dict = {}
for col in cat_cols:
    mentalHealth_data = pd.concat([mentalHealth_data.drop(col, axis=1), pd.get_dummies(mentalHealth_data[col], prefix=col, drop_first=True)], axis=1)

In [12]:
mentalHealth_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 663 entries, 0 to 662
Data columns (total 62 columns):
 #   Column                                                               Non-Null Count  Dtype  
---  ------                                                               --------------  -----  
 0   concimiento_cubrimiento_EM                                           663 non-null    int64  
 1   habla_jefe_EM_flag                                                   663 non-null    float64
 2   hablar_companeros_EM_flag                                            663 non-null    float64
 3   hablar_companeros_EM_conmigo                                         663 non-null    float64
 4   importacia_salud_fisica                                              663 non-null    float64
 5   importancia_salud_mental                                             663 non-null    float64
 6   trabajado_otras_empresa                                              663 non-null    int64  
 7   empresa_

In [13]:
from pandas_profiling import ProfileReport
profile2 = ProfileReport(mentalHealth_data, title="Diabetes data Profiling Report 2" )
profile2.to_notebook_iframe()

Render HTML: 100%|██████████| 1/1 [00:05<00:00,  5.51s/it]


In [14]:
profile2.to_file("../reports/Diabetes_data_profiling_bivariate_report_2.html")

Export report to file: 100%|██████████| 1/1 [00:00<00:00, 13.70it/s]


# Entradas y salidas

In [15]:
X = mentalHealth_data.drop("tiene_EM", axis=1)
y= mentalHealth_data["tiene_EM"]

# Dividir los datos 70/30
Dado que la variable objetivo está tan desbalanceada, es necesario utilizar stratify para asegurarse de que tome una muestra representativa de los datos

In [16]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.3,random_state =42, stratify=y)

In [17]:
#Se verifica que tanto en el dataset de entrenamiento como en el de prueba, exista una cantidad similar de valores positivos 
perc_test = y_test.value_counts()[1]*100/len(y_test)
perc_train = y_train.value_counts()[1]*100/len(y_train)

print(f" Porcentaje de positivos en el dataset de prueba={perc_test} , dataset de entrenamiento={perc_train}")

 Porcentaje de positivos en el dataset de prueba=68.84422110552764 , dataset de entrenamiento=69.18103448275862


# Selección de la medida
Hacer un mal diagnostico de una enfermedad mental puede llegar a tener efectos negativos en las personas, como:

- Confusión
- Medicación incorrecta
- Alteración hormonal
- Empeorar la condición del paciente y generar nuevas enfermedades

[Psychology today](https://www.psychologytoday.com/us/blog/experimentations/201805/6-reasons-common-psych-diagnostic-mistakes)

[Healing and hope for children and families](https://hside.org/impact-of-mental-health-misdiagnosis/)

Por esta razón, es mucho más beneficioso para este análisis tener verdaderos positivos que verdaderos negativos, utilizando la medida:

> ** Precision **


In [18]:
#Medidas
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score

In [19]:
#algoritmos
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier

# Selección del modelo

In [32]:
seed =2
models = []

#logistic Regression
models.append(('LR', LogisticRegression(solver='liblinear')))

# Decision Tree classifier
models.append(('TREE', DecisionTreeClassifier()))

# Naïve Bayes
models.append(('NB', GaussianNB()))
# SVM
models.append(('SVM', SVC(C=1.0, kernel='rbf', max_iter=1000, tol=1e-3)))

#Random forest
models.append(('Random forest', RandomForestClassifier(max_depth=2, random_state=0)))
# evaluate each model in turn
results = []
names = []
scoring = 'precision'
for name, model in models:
	# Kfol cross validation for model selection
	kfold = model_selection.KFold(n_splits=10, random_state=seed)
	#X train , y train
	cv_results = model_selection.cross_val_score(model, X_train, y_train, cv=kfold, scoring=scoring)
	results.append(cv_results)
	names.append(name)
	msg = f"({name}, {cv_results.mean()}, {cv_results.std()})"
	print(msg)

(LR, 0.8938995082782297, 0.04358058458762407)
(TREE, 0.8536263240928555, 0.057686503096044235)
(NB, 0.9013857916791732, 0.052057729060921855)
(SVM, 0.6919056429232193, 0.05938428469061665)
(Random forest, 0.8744296562057847, 0.048923385014751665)


In [33]:
result_df = pd.DataFrame(results, index=names).T
px.box(result_df,title = 'Algorithm Comparison')

Se escoge el naive bayes, su máximo es del 96% y su minimo del 80%. No se elige el random forest porque está hecho para datos muy grandes y puede terminar en overfitting

In [34]:
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler

In [39]:
# Naïve Bayes with standardscaler
NB_pipeline = make_pipeline( StandardScaler(), GaussianNB())
models.append(('NB_pipeline', NB_pipeline))

In [40]:
scoring = 'precision'
name, model
# Kfol cross validation for model selection
kfold = model_selection.KFold(n_splits=10, random_state=seed)
#X train , y train
cv_results = model_selection.cross_val_score(NB_pipeline, X_train, y_train, cv=kfold, scoring=scoring)
results.append(cv_results)
names.append('NB_pipeline')
msg = f"({'NB_pipeline'}, {cv_results.mean()}, {cv_results.std()}"
print(msg)

(NB_pipeline, 0.9007392399550354, 0.05164368315541412


# Hperparametrización
Se hace con gridsearch, buscando los mejores parametros

In [50]:
#calculos previos, se imprime la el porcentaje de negativos y positivos en el dataset 
y.value_counts()/len(y)

1    0.690799
0    0.309201
Name: tiene_EM, dtype: float64

In [51]:
a,b = y.value_counts()/len(y)

In [52]:
#Se corre el modelo con los mejores parametros
from sklearn.model_selection import GridSearchCV
parameters = {'priors': [None, [a,b]]}

grid_search = GridSearchCV(GaussianNB(), parameters, cv=10, return_train_score=True)
grid_search.fit(X_train, y_train)

grid_search.best_params_

{'priors': [0.6907993966817496, 0.3092006033182504]}

Puede verse que los porcentajes de valores negativos y positivos del datset original son muy similares a los del modelo con los mejores parametros encontrados con gridsearch

# Matriz de confusió